Problem:
With new york being the financial capital of usa and a very popular tourist attraction, it would be interesting to see what places in new york are most frequently visited. For that using the new york city data that have been used earlier in this course (https://cocl.us/new_york_dataset) and foursquare api, I am going to  going to try to determine top 10 most commonly visited places in each neighbourhoods of new york in order to determine which areas are more popular, diverse and accessible than others. This can help me to also figure out if a person wants to start a new restaurant which neighbourhoods would be more appropriate for that.

To start I will import all the libraries that I have learned to use so far.

In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Fetching package metadata .............
Solving package specifications: .

Package plan for installation in environment /opt/conda/envs/DSX-Python35:

The following NEW packages will be INSTALLED:

    geographiclib: 1.49-py_0   conda-forge
    geopy:         1.18.1-py_0 conda-forge

geographiclib- 100% |################################| Time: 0:00:00  24.08 MB/s
geopy-1.18.1-p 100% |################################| Time: 0:00:00  36.29 MB/s
Fetching package metadata .............
Solving package specifications: .

Package plan for installation in environment /opt/conda/envs/DSX-Python35:

The following NEW packages will be INSTALLED:

    altair:  2.2.2-py35_1 conda-forge
    branca:  0.3.1-py_0   conda-forge
    folium:  0.5.0-py_0   conda-forge
    vincent: 0.4.4-py_1   conda-forge

altair-2.2.2-p 100% |################################| Time: 0:00:00  47.62 MB/s
branca-0.3.1-p 100% |################################| Time: 0:00:00  31.60 MB/s
vincent-0.4.4- 100% |###################

Data:
Since the neighbourhood consists of 5 boroughs and 306 neighbourhoods, and I would need lattitude and longitude information of all, I am going to rely on the same data that we have used earlier in the course. e.g. https://cocl.us/new_york_dataset. I am simply going to do a wget, as we did in the course earlier, to get the data.

In [3]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [4]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [5]:
newyork_data

{'bbox': [-74.2492599487305,
  40.5033187866211,
  -73.7061614990234,
  40.9105606079102],
 'crs': {'properties': {'name': 'urn:ogc:def:crs:EPSG::4326'}, 'type': 'name'},
 'features': [{'geometry': {'coordinates': [-73.84720052054902,
     40.89470517661],
    'type': 'Point'},
   'geometry_name': 'geom',
   'id': 'nyu_2451_34572.1',
   'properties': {'annoangle': 0.0,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661],
    'borough': 'Bronx',
    'name': 'Wakefield',
    'stacked': 1},
   'type': 'Feature'},
  {'geometry': {'coordinates': [-73.82993910812398, 40.87429419303012],
    'type': 'Point'},
   'geometry_name': 'geom',
   'id': 'nyu_2451_34572.2',
   'properties': {'annoangle': 0.0,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.874294193

In [7]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [10]:
neighborhoods_data = newyork_data['features']
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [11]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [12]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


As in the course, using geopy library we are going to get the co-ordinates of new york city

In [13]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7308619, -73.9871558.


Now generate the map of new york using the lattitude and longitude data

In [14]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

Now I am going to use Foresquare api to get venues around new york city

In [15]:
CLIENT_ID = 'F4D5H5GZR5DRAA5WV2DZA52BRMKAOU1GNK3HAS1TIWDHXWGS' # your Foursquare ID
CLIENT_SECRET = 'FA44EPGPPTA5SSM545S1G3IAKGAGRFSZQYNZUZ4BGKCVH4HE' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: F4D5H5GZR5DRAA5WV2DZA52BRMKAOU1GNK3HAS1TIWDHXWGS
CLIENT_SECRET:FA44EPGPPTA5SSM545S1G3IAKGAGRFSZQYNZUZ4BGKCVH4HE


In [16]:
neighborhoods.loc[0, 'Neighborhood']

'Wakefield'

In [18]:
# type your answer here
LIMIT = 100 # limit of number of venues returned by Foursquare API

radius = 500 # define radius
# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    latitude, 
    longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=F4D5H5GZR5DRAA5WV2DZA52BRMKAOU1GNK3HAS1TIWDHXWGS&client_secret=FA44EPGPPTA5SSM545S1G3IAKGAGRFSZQYNZUZ4BGKCVH4HE&v=20180605&ll=40.7308619,-73.9871558&radius=500&limit=100'

In [19]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [20]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5c48a2ccdb04f57d55175c47'},
 'response': {'groups': [{'items': [{'reasons': {'count': 0,
       'items': [{'reasonName': 'globalInteractionReason',
         'summary': 'This spot is popular',
         'type': 'general'}]},
      'referralId': 'e-0-3fd66200f964a5203de41ee3-0',
      'venue': {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/nightlife/sake_',
          'suffix': '.png'},
         'id': '4bf58dd8d48988d11c941735',
         'name': 'Sake Bar',
         'pluralName': 'Sake Bars',
         'primary': True,
         'shortName': 'Sake Bar'}],
       'id': '3fd66200f964a5203de41ee3',
       'location': {'address': '240 E 9th St',
        'cc': 'US',
        'city': 'New York',
        'country': 'United States',
        'crossStreet': 'btwn 2nd & 3rd Ave.',
        'distance': 168,
        'formattedAddress': ['240 E 9th St (btwn 2nd & 3rd Ave.)',
         'New York, NY 10003',
         'United States'],
        'l

In [21]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name           categories        lat        lng
0              Sake Bar Decibel             Sake Bar  40.729418 -73.987769
1             Momofuku Ssäm Bar     Asian Restaurant  40.731718 -73.985554
2                   Han Dynasty   Chinese Restaurant  40.732130 -73.988090
3  Hi-Collar - ハイカラ (Hi-Collar)          Coffee Shop  40.729449 -73.985918
4            Casey Rubber Stamp  Arts & Crafts Store  40.729962 -73.985098

In [22]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


In [23]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [24]:
ny_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [26]:
print(ny_venues.shape)
ny_venues.head()

(10236, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896521       -73.844680        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3     Dunkin Donuts       40.890631       -73.849027      Donut Shop  
4            SUBWAY       40.890656       -73.849192  Sandwich Place

In [27]:
ny_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      29                      29   
Annadale                                      10                      10   
Arden Heights                                  4                       4   
Arlington                                      8                       8   
Arrochar                                      18                      18   
Arverne                                       15                      15   
Astoria                                      100                     100   
Astoria Heights                               13                      13   
Auburndale                                    22                      22   
Bath Beach                                    49                      49   
Battery Park City                            100                     100   
Bay Ridge                                     90                      90   
Bay Terrace                                   48                      48   
Baychester                                    19                      19   
Bayside                                       74                      74   
Bayswater                                      3                       3   
Bedford Park                                  43                      43   
Bedford Stuyvesant                            26                      26   
Beechhurst                                    15                      15   
Bellaire                                      12                      12   
Belle Harbor                                  18                      18   
Bellerose                                     20                      20   
Belmont                                       98                      98   
Bensonhurst                                   23                      23   
Bergen Beach                                   7                       7   
Blissville                                    18                      18   
Bloomfield                                     4                       4   
Boerum Hill                                   83                      83   
Borough Park                                  21                      21   
Breezy Point                                   4                       4   
Briarwood                                     15                      15   
Brighton Beach                                43                      43   
Broad Channel                                  5                       5   
Broadway Junction                             18                      18   
Bronxdale                                     14                      14   
Brooklyn Heights                             100                     100   
Brookville                                     1                       1   
Brownsville                                   16                      16   
Bulls Head                                    42                      42   
Bushwick                                      75                      75   
Butler Manor                                   7                       7   
Cambria Heights                               14                      14   
Canarsie                                       8                       8   
Carnegie Hill                                100                     100   
Carroll Gardens                              100                     100   
Castle Hill                                    8                       8   
Castleton Corners                             15                      15   
Central Harlem                                44                      44   
Charleston                                    29                      29   
Chelsea                                      104                     104   
Chinatown                                    100                     100   

In [28]:
print('There are {} uniques categories.'.format(len(ny_venues['Venue Category'].unique())))

There are 424 uniques categories.


Analyze each neighbourhoods of NYC:

In [38]:
# one hot encoding
ny_onehot = pd.get_dummies(ny_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
ny_onehot['Neighborhood'] = ny_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [ny_onehot.columns[-1]] + list(ny_onehot.columns[:-1])
ny_onehot = ny_onehot[fixed_columns]
ny_onehot.dtypes
print('{} rows were returned after one hot encoding.'.format(ny_onehot.shape[0]))
ny_onehot.head()

10236 rows were returned after one hot encoding.


Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  Airport Terminal  Airport Tram  American Restaurant  \
0                   0                 0             0                    0   
1                   0                 0             0                    0   
2                   0                 0             0                    0   
3                   0                 0             0                    0   
4                   0                 0             0                    0   

   Animal Shelter  Antique Shop  Arcade  Arepa Restaurant  \
0               0             0       0                 0   
1               0             0       0                 0   
2               0             0       0                 0   
3               0             0       0                 0   
4               0             0       0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auditorium  \
0                     0                 0                   0           0   
1                     0                 0                   0           0   
2                     0                 0                   0           0   
3                     0                 0                   0           0   
4                     0                 0                   0           0   

   Australian Restaurant  Austrian Restaurant  Auto Workshop  Automotive Shop  \
0                      0                    0              0                0   
1                      0                    0              0                0   
2                      0                    0              0                0   
3                      0                    0              0                0   
4                      0                    0              0                0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0           0           0       0     0    0               0   
1          0           0           0       0     0    0               0   
2          0           0           0       0     0    0               0   
3          0           0           0       0     0    0               0   
4          0           0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Bath House  Beach  Beach Bar  \
0                 0                 0           0      0          0   
1                 0                 0           0      0          0   
2                 0                 0           0      0          0   
3                 0                 0           0      0          0   
4                 0                 0           0      0          0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Belgian Restaurant  \
0                0         0            0           0                   0   
1                0         0            0           0                   0   
2                0         0            0           0                   0   
3                0         0            0           0                   0   
4                0         0            0           0                 

dataframe size is:

In [30]:
ny_onehot.shape

(10236, 424)

Now we would group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [40]:
ny_grouped = ny_onehot.groupby('Neighborhood').mean().reset_index()
ny_grouped


Neighborhood  Yoga Studio  Accessories Store  \
0                     Allerton     0.000000           0.000000   
1                     Annadale     0.000000           0.000000   
2                Arden Heights     0.000000           0.000000   
3                    Arlington     0.000000           0.000000   
4                     Arrochar     0.000000           0.000000   
5                      Arverne     0.000000           0.000000   
6                      Astoria     0.000000           0.000000   
7              Astoria Heights     0.000000           0.000000   
8                   Auburndale     0.000000           0.000000   
9                   Bath Beach     0.000000           0.000000   
10           Battery Park City     0.000000           0.000000   
11                   Bay Ridge     0.000000           0.000000   
12                 Bay Terrace     0.000000           0.020833   
13                  Baychester     0.000000           0.000000   
14                     Bayside     0.013514           0.000000   
15                   Bayswater     0.000000           0.000000   
16                Bedford Park     0.000000           0.000000   
17          Bedford Stuyvesant     0.000000           0.000000   
18                  Beechhurst     0.066667           0.000000   
19                    Bellaire     0.000000           0.000000   
20                Belle Harbor     0.000000           0.000000   
21                   Bellerose     0.000000           0.000000   
22                     Belmont     0.000000           0.000000   
23                 Bensonhurst     0.000000           0.000000   
24                Bergen Beach     0.000000           0.000000   
25                  Blissville     0.000000           0.000000   
26                  Bloomfield     0.000000           0.000000   
27                 Boerum Hill     0.024096           0.000000   
28                Borough Park     0.000000           0.000000   
29                Breezy Point     0.000000           0.000000   
30                   Briarwood     0.000000           0.000000   
31              Brighton Beach     0.000000           0.000000   
32               Broad Channel     0.000000           0.000000   
33           Broadway Junction     0.000000           0.000000   
34                   Bronxdale     0.000000           0.000000   
35            Brooklyn Heights     0.050000           0.000000   
36                  Brookville     0.000000           0.000000   
37                 Brownsville     0.000000           0.000000   
38                  Bulls Head     0.000000           0.000000   
39                    Bushwick     0.000000           0.000000   
40                Butler Manor     0.000000           0.000000   
41             Cambria Heights     0.000000           0.000000   
42                    Canarsie     0.000000           0.000000   
43               Carnegie Hill     0.030000           0.000000   
44             Carroll Gardens     0.000000           0.000000   
45                 Castle Hill     0.000000           0.000000   
46           Castleton Corners     0.000000           0.000000   
47              Central Harlem     0.000000           0.000000   
48                  Charleston     0.000000           0.000000   
49                     Chelsea     0.000000           0.000000   
50                   Chinatown     0.010000           0.000000   
51                 City Island     0.000000           0.000000   
52                   City Line     0.000000           0.000000   
53                Civic Center     0.030000           0.000000   
54           Claremont Village     0.000000           0.000000   
55                Clason Point     0.000000           0.000000   
56                     Clifton     0.000000           0.000000   
57                     Clinton     0.000000           0.000000   
58                Clinton Hill     0.031579           0.000000   
59                  Co-op City     0.000000           0.06

In [41]:
print('{} rows were returned after grouping.'.format(ny_grouped.shape[0]))
ny_grouped.shape

302 rows were returned after grouping.


(302, 424)

In [42]:
num_top_venues = 5

for hood in ny_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = ny_grouped[ny_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
                venue  freq
0         Supermarket  0.10
1         Pizza Place  0.10
2  Chinese Restaurant  0.07
3       Deli / Bodega  0.07
4         Bus Station  0.07


----Annadale----
                 venue  freq
0  American Restaurant   0.2
1          Pizza Place   0.2
2           Restaurant   0.1
3                Diner   0.1
4           Sports Bar   0.1


----Arden Heights----
                  venue  freq
0              Pharmacy  0.25
1           Pizza Place  0.25
2           Coffee Shop  0.25
3              Bus Stop  0.25
4  Pakistani Restaurant  0.00


----Arlington----
                 venue  freq
0         Intersection  0.12
1          Coffee Shop  0.12
2        Deli / Bodega  0.12
3         Food Service  0.12
4  American Restaurant  0.12


----Arrochar----
                venue  freq
0            Bus Stop  0.17
1       Deli / Bodega  0.11
2  Italian Restaurant  0.11
3        Liquor Store  0.06
4          Food Truck  0.06


----Arverne----
           venue  f

                  venue  freq
0    African Restaurant  0.07
1    Chinese Restaurant  0.05
2   American Restaurant  0.05
3  Gym / Fitness Center  0.05
4        Cosmetics Shop  0.05


----Charleston----
            venue  freq
0   Big Box Store  0.07
1      Shoe Store  0.07
2  Cosmetics Shop  0.07
3   Grocery Store  0.03
4    Burger Joint  0.03


----Chelsea----
                venue  freq
0         Coffee Shop  0.07
1  Italian Restaurant  0.06
2      Ice Cream Shop  0.05
3             Theater  0.04
4              Bakery  0.04


----Chinatown----
                 venue  freq
0   Chinese Restaurant  0.09
1      Bubble Tea Shop  0.06
2   Dim Sum Restaurant  0.04
3  American Restaurant  0.04
4         Cocktail Bar  0.04


----City Island----
                    venue  freq
0         Harbor / Marina  0.11
1      Seafood Restaurant  0.07
2                    Park  0.07
3  Thrift / Vintage Store  0.07
4          History Museum  0.04


----City Line----
          venue  freq
0    Donut Shop  0.

                        venue  freq
0  Construction & Landscaping   0.5
1            Sculpture Garden   0.5
2                 Yoga Studio   0.0
3           Paella Restaurant   0.0
4                   Pet Store   0.0


----Erasmus----
                  venue  freq
0  Caribbean Restaurant  0.19
1                   Bar  0.10
2           Yoga Studio  0.05
3     Convenience Store  0.05
4     Health Food Store  0.05


----Far Rockaway----
                venue  freq
0         Pizza Place  0.13
1       Deli / Bodega  0.10
2       Grocery Store  0.10
3  Chinese Restaurant  0.06
4         Supermarket  0.06


----Fieldston----
               venue  freq
0              River  0.33
1         Playground  0.33
2              Plaza  0.33
3        Yoga Studio  0.00
4  Paella Restaurant  0.00


----Financial District----
         venue  freq
0  Coffee Shop  0.09
1        Hotel  0.05
2    Wine Shop  0.04
3   Steakhouse  0.04
4          Gym  0.04


----Flatbush----
                  venue  freq
0  Caribb

                venue  freq
0         Coffee Shop  0.08
1                Café  0.07
2  Italian Restaurant  0.07
3               Hotel  0.05
4          Restaurant  0.05


----Huguenot----
                venue  freq
0                Bank  0.22
1          Donut Shop  0.11
2  Italian Restaurant  0.11
3              Lawyer  0.11
4      Ice Cream Shop  0.11


----Hunters Point----
                 venue  freq
0   Italian Restaurant  0.05
1                 Café  0.05
2  Japanese Restaurant  0.04
3              Brewery  0.04
4     Asian Restaurant  0.03


----Hunts Point----
            venue  freq
0            Bank   0.1
1  Waste Facility   0.1
2  Farmers Market   0.1
3          Bakery   0.1
4       BBQ Joint   0.1


----Inwood----
                venue  freq
0  Mexican Restaurant  0.07
1                Café  0.07
2         Pizza Place  0.05
3              Lounge  0.05
4                Park  0.04


----Jackson Heights----
                       venue  freq
0  Latin American Restaurant  0.11


          venue  freq
0          Lake   0.5
1          Pool   0.5
2   Yoga Studio   0.0
3  Outlet Store   0.0
4   Pet Service   0.0


----Morningside Heights----
                 venue  freq
0          Coffee Shop  0.12
1            Bookstore  0.07
2  American Restaurant  0.07
3                 Park  0.07
4         Burger Joint  0.05


----Morris Heights----
                venue  freq
0  Spanish Restaurant  0.18
1                Bank  0.09
2          Food Truck  0.09
3       Grocery Store  0.09
4            Pharmacy  0.09


----Morris Park----
           venue  freq
0    Pizza Place  0.20
1  Deli / Bodega  0.08
2   Burger Joint  0.08
3         Bakery  0.08
4    Supermarket  0.04


----Morrisania----
                  venue  freq
0        Discount Store  0.17
1              Pharmacy  0.07
2         Metro Station  0.07
3            Donut Shop  0.07
4  Fast Food Restaurant  0.07


----Mott Haven----
              venue  freq
0       Pizza Place  0.10
1               Gym  0.10
2        Do

                venue  freq
0  Chinese Restaurant  0.16
1              Bakery  0.08
2                Bank  0.08
3  Frozen Yogurt Shop  0.04
4          Bagel Shop  0.04


----Queensbridge----
                venue  freq
0               Hotel  0.33
1      Sandwich Place  0.13
2                Park  0.07
3      Scenic Lookout  0.07
4  Spanish Restaurant  0.07


----Randall Manor----
         venue  freq
0     Bus Stop   0.4
1   Bagel Shop   0.2
2  Pizza Place   0.2
3         Park   0.2
4  Yoga Studio   0.0


----Ravenswood----
                 venue  freq
0        Grocery Store  0.07
1   Chinese Restaurant  0.07
2  Japanese Restaurant  0.04
3           Taco Place  0.04
4            BBQ Joint  0.04


----Red Hook----
                 venue  freq
0          Art Gallery  0.10
1   Seafood Restaurant  0.08
2                 Café  0.06
3                 Park  0.06
4  American Restaurant  0.04


----Rego Park----
                venue  freq
0              Bakery  0.10
1       Grocery Store  0.08

                       venue  freq
0         Mexican Restaurant  0.09
1                Pizza Place  0.09
2  Latin American Restaurant  0.09
3                       Bank  0.09
4                     Bakery  0.09


----Sutton Place----
                    venue  freq
0    Gym / Fitness Center  0.06
1      Italian Restaurant  0.05
2               Juice Bar  0.04
3  Furniture / Home Store  0.04
4       Indian Restaurant  0.04


----Throgs Neck----
                venue  freq
0       Deli / Bodega   0.2
1         Pizza Place   0.1
2           Juice Bar   0.1
3    Asian Restaurant   0.1
4  Italian Restaurant   0.1


----Todt Hill----
                venue  freq
0               Trail   0.5
1                Park   0.5
2  Photography Studio   0.0
3           Pet Store   0.0
4         Pet Service   0.0


----Tompkinsville----
                    venue  freq
0                Bus Stop  0.08
1             Pizza Place  0.08
2               Gastropub  0.04
3              Food Truck  0.04
4  Thrift / V

In [46]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now we will create the new dataframe and display the top 5 venues for each neighborhood.

In [69]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_df = pd.DataFrame(columns=columns)
neighborhoods_venues_df['Neighborhood'] = ny_grouped['Neighborhood']

for ind in np.arange(ny_grouped.shape[0]):
    neighborhoods_venues_df.iloc[ind, 1:] = return_most_common_venues(ny_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_df.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Supermarket           Pizza Place   
1       Annadale           Pizza Place   American Restaurant   
2  Arden Heights              Pharmacy           Pizza Place   
3      Arlington   American Restaurant           Coffee Shop   
4       Arrochar              Bus Stop    Italian Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Bus Station         Deli / Bodega    Chinese Restaurant   
1         Train Station                Bakery          Dance Studio   
2           Coffee Shop              Bus Stop   Filipino Restaurant   
3          Intersection          Liquor Store         Deli / Bodega   
4         Deli / Bodega            Food Truck                 Hotel   

       6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                        Spa        Cosmetics Shop         Grocery Store   
1                 Restaurant            Sports Bar                 Diner   
2                Event Space               Exhibit            Eye Doctor   
3                 Playground          Food Service         Boat or Ferry   
4  Middle Eastern Restaurant              Pharmacy            Bagel Shop   

  9th Most Common Venue 10th Most Common Venue  
0            Bike Trail    Fried Chicken Joint  
1                 Field   Fast Food Restaurant  
2               Factory     Falafel Restaurant  
3        Farmers Market                  Field  
4          Liquor Store         Sandwich Place

Kmean cluster New York City

In [61]:
# set number of clusters
kclusters = 5

manhattan_grouped_clustering = ny_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(ny_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 3, 0, 1, 0, 0, 0, 0, 0], dtype=int32)

In [70]:
# add clustering labels
neighborhoods_venues_df.insert(0, 'Cluster Labels', kmeans.labels_)

ny_merged = neighborhoods

ny_merged = ny_merged.join(neighborhoods_venues_df.set_index('Neighborhood'), on='Neighborhood')

ny_merged.head(1000) 

Borough               Neighborhood   Latitude  Longitude  \
0            Bronx                  Wakefield  40.894705 -73.847201   
1            Bronx                 Co-op City  40.874294 -73.829939   
2            Bronx                Eastchester  40.887556 -73.827806   
3            Bronx                  Fieldston  40.895437 -73.905643   
4            Bronx                  Riverdale  40.890834 -73.912585   
5            Bronx                Kingsbridge  40.881687 -73.902818   
6        Manhattan                Marble Hill  40.876551 -73.910660   
7            Bronx                   Woodlawn  40.898273 -73.867315   
8            Bronx                    Norwood  40.877224 -73.879391   
9            Bronx             Williamsbridge  40.881039 -73.857446   
10           Bronx                 Baychester  40.866858 -73.835798   
11           Bronx             Pelham Parkway  40.857413 -73.854756   
12           Bronx                City Island  40.847247 -73.786488   
13           Bronx               Bedford Park  40.870185 -73.885512   
14           Bronx         University Heights  40.855727 -73.910416   
15           Bronx             Morris Heights  40.847898 -73.919672   
16           Bronx                    Fordham  40.860997 -73.896427   
17           Bronx               East Tremont  40.842696 -73.887356   
18           Bronx                 West Farms  40.839475 -73.877745   
19           Bronx               High  Bridge  40.836623 -73.926102   
20           Bronx                    Melrose  40.819754 -73.909422   
21           Bronx                 Mott Haven  40.806239 -73.916100   
22           Bronx                Port Morris  40.801664 -73.913221   
23           Bronx                   Longwood  40.815099 -73.895788   
24           Bronx                Hunts Point  40.809730 -73.883315   
25           Bronx                 Morrisania  40.823592 -73.901506   
26           Bronx                  Soundview  40.821012 -73.865746   
27           Bronx               Clason Point  40.806551 -73.854144   
28           Bronx                Throgs Neck  40.815109 -73.816350   
29           Bronx               Country Club  40.844246 -73.824099   
30           Bronx                Parkchester  40.837938 -73.856003   
31           Bronx         Westchester Square  40.840619 -73.842194   
32           Bronx                   Van Nest  40.843608 -73.866299   
33           Bronx                Morris Park  40.847549 -73.850402   
34           Bronx                    Belmont  40.857277 -73.888452   
35           Bronx             Spuyten Duyvil  40.881395 -73.917190   
36           Bronx            North Riverdale  40.908543 -73.904531   
37           Bronx                 Pelham Bay  40.850641 -73.832074   
38           Bronx              Schuylerville  40.826580 -73.826203   
39           Bronx             Edgewater Park  40.821986 -73.813885   
40           Bronx                Castle Hill  40.819014 -73.848027   
41           Bronx                  Olinville  40.871371 -73.863324   
42           Bronx             Pelham Gardens  40.862966 -73.841612   
43           Bronx                  Concourse  40.834284 -73.915589   
44           Bronx                  Unionport  40.829774 -73.850535   
45           Bronx                   Edenwald  40.884561 -73.848083   
46        Brooklyn                  Bay Ridge  40.625801 -74.030621   
47        Brooklyn                Bensonhurst  40.611009 -73.995180   
48        Brooklyn                Sunset Park  40.645103 -74.010316   
49        Brooklyn                 Greenpoint  40.730201 -73.954241   
50        Brooklyn                  Gravesend  40.595260 -73.973471   
51        Brooklyn             Brighton Beach  40.576825 -73.965094   
52        Brooklyn             Sheepshead Bay  40.586890 -73.943186   
53        Brooklyn          Manhattan Terrace  40.614433 -73.957438   
54        Brooklyn                   Flatbush  40.636326 -73.958401   
55        Brooklyn              Cro

Now we visualize the cluster

In [72]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(ny_merged['Latitude'], ny_merged['Longitude'], ny_merged['Neighborhood'], ny_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

Examine the clusters

CLUSTER 1

In [73]:
ny_merged.loc[ny_merged['Cluster Labels'] == 0, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood        1st Most Common Venue  \
0                    Wakefield                   Laundromat   
1                   Co-op City               Mattress Store   
2                  Eastchester                  Bus Station   
3                    Fieldston                        River   
4                    Riverdale                         Bank   
5                  Kingsbridge                  Pizza Place   
6                  Marble Hill               Discount Store   
7                     Woodlawn                   Playground   
8                      Norwood                  Pizza Place   
9               Williamsbridge                    Nightclub   
10                  Baychester                  Pizza Place   
11              Pelham Parkway           Italian Restaurant   
12                 City Island              Harbor / Marina   
13                Bedford Park           Chinese Restaurant   
14          University Heights                  Pizza Place   
15              Morris Heights           Spanish Restaurant   
16                     Fordham                  Pizza Place   
17                East Tremont                  Pizza Place   
18                  West Farms                  Bus Station   
19                High  Bridge                     Pharmacy   
20                     Melrose                  Pizza Place   
21                  Mott Haven                          Gym   
22                 Port Morris                      Brewery   
24                 Hunts Point                         Café   
25                  Morrisania               Discount Store   
26                   Soundview           Chinese Restaurant   
27                Clason Point                         Park   
29                Country Club               Sandwich Place   
30                 Parkchester                  Supermarket   
31          Westchester Square                  Pizza Place   
33                 Morris Park                  Pizza Place   
34                     Belmont           Italian Restaurant   
35              Spuyten Duyvil                         Park   
36             North Riverdale                  Pizza Place   
37                  Pelham Bay           Italian Restaurant   
38               Schuylerville           Mexican Restaurant   
39              Edgewater Park           Italian Restaurant   
40                 Castle Hill                       Market   
41                   Olinville                  Supermarket   
42              Pelham Gardens                  Bus Station   
43                   Concourse                       Bakery   
44                   Unionport                   Donut Shop   
46                   Bay Ridge           Italian Restaurant   
47                 Bensonhurst                  Pizza Place   
48                 Sunset Park                       Bakery   
49                  Greenpoint                          Bar   
50                   Gravesend           Italian Restaurant   
51              Brighton Beach  Eastern European Restaurant   
52              Sheepshead Bay                 Dessert Shop   
53           Manhattan Terrace                  Pizza Place   
54                    Flatbush           Mexican Restaurant   
55               Crown Heights                  Pizza Place   
56               East Flatbush                         Food   
57                  Kensington              Thai Restaurant   
58             Windsor Terrace                   Food Truck   
59            Prospect Heights                          Bar   
60                 Brownsville                   Restaurant   
61                Williamsburg                          Bar   
62                    Bushwick                          Bar   
63          Bedford Stuyvesant                  Coffee Shop   
64            Brooklyn Heights                  Yoga Studio   
65                 Cobble Hill                  Pizza Place   
66             Carroll Gardens           Italian 

CLUSTER 2

In [74]:
ny_merged.loc[ny_merged['Cluster Labels'] == 1, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood 1st Most Common Venue       2nd Most Common Venue  \
23           Longwood         Deli / Bodega              Sandwich Place   
28        Throgs Neck         Deli / Bodega            Asian Restaurant   
32           Van Nest           Pizza Place               Deli / Bodega   
45           Edenwald           Supermarket  Construction & Landscaping   
72      East New York    Chinese Restaurant               Deli / Bodega   
80       Borough Park         Deli / Bodega                 Pizza Place   
83        Marine Park        Baseball Field            Basketball Court   
89         Ocean Hill         Deli / Bodega                        Food   
148  South Ozone Park                  Park               Deli / Bodega   
150        Whitestone       Bubble Tea Shop                       Train   
171     Broad Channel              Dive Bar               Deli / Bodega   
190      Belle Harbor                 Beach                    Boutique   
193        Brookville         Deli / Bodega               Women's Store   
194          Bellaire         Deli / Bodega          Chinese Restaurant   
195      North Corona         Deli / Bodega        Gym / Fitness Center   
204       South Beach         Deli / Bodega                        Pier   
206  Mariner's Harbor    Italian Restaurant               Deli / Bodega   
210            Travis         Deli / Bodega               Bowling Alley   
217       Tottenville              Bus Stop          Italian Restaurant   
228          Arrochar              Bus Stop          Italian Restaurant   
232     Midland Beach         Deli / Bodega                  Restaurant   
234    New Dorp Beach    Italian Restaurant               Deli / Bodega   
252       Shore Acres    Italian Restaurant                    Bus Stop   
264            Utopia         Deli / Bodega            Basketball Court   
270        Mount Hope         Deli / Bodega                 Supermarket   
284     Manor Heights         Deli / Bodega                  Donut Shop   
288           Roxbury                 Beach                   Irish Pub   
296           Madison            Bagel Shop               Deli / Bodega   

    3rd Most Common Venue            4th Most Common Venue  \
23          Grocery Store                       Donut Shop   
28                    Bar               Italian Restaurant   
32                 Bakery                       Donut Shop   
45          Deli / Bodega                    Grocery Store   
72          Metro Station                              Gym   
80                   Bank                         Pharmacy   
83          Deli / Bodega                   Ice Cream Shop   
89            Supermarket  Southern / Soul Food Restaurant   
148                  Food                   Sandwich Place   
150         Deli / Bodega                    Moving Target   
171           Pizza Place                      Bus Station   
190         Deli / Bodega                              Spa   
193           Fish Market                          Exhibit   
194              Bus Stop                     Intersection   
195                Bakery                      Pizza Place   
204                 Beach               Athletics & Sports   
206              Bus Stop                Other Repair Shop   
210                 Hotel                      Pizza Place   
217        Cosmetics Shop           Thrift / Vintage Store   
228         Deli / Bodega                       Food Truck   
232                 Beach                     Dessert Shop   
234            Sports Bar                            Beach   
252          Intersection                    Deli / Bodega   
264    Chinese Restaurant                           Bakery   
270        Sandwich Place                 Video Game Store   
284            Campground                     Home Service   
288                 Trail                    Deli / Bodega   
296          Dessert Shop                              Spa   

    5th Most Common Venue      6th

CLUSTER 3

In [75]:
ny_merged.loc[ny_merged['Cluster Labels'] == 2, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
207   Port Ivory                   Bar         Women's Store   
212      Oakwood                   Bar         Women's Store   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
207  Ethiopian Restaurant               Exhibit            Eye Doctor   
212  Ethiopian Restaurant               Exhibit            Eye Doctor   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
207               Factory    Falafel Restaurant                  Farm   
212               Factory    Falafel Restaurant                  Farm   

    9th Most Common Venue 10th Most Common Venue  
207        Farmers Market   Fast Food Restaurant  
212        Farmers Market   Fast Food Restaurant

CLUSTER 4

In [76]:
ny_merged.loc[ny_merged['Cluster Labels'] == 3, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
77   Manhattan Beach                  Café              Bus Stop   
198     New Brighton              Bus Stop                  Park   
202      Grymes Hill               Dog Run      Basketball Court   
205    Port Richmond   Rental Car Location      Basketball Court   
224        Park Hill              Bus Stop                 Hotel   
229         Grasmere              Bus Stop            Bagel Shop   
241    Arden Heights              Pharmacy           Pizza Place   
242       Greenridge           Pizza Place        Ice Cream Shop   
245       Bloomfield        Discount Store     Recreation Center   
256    Randall Manor              Bus Stop            Bagel Shop   
258         Elm Park              Bus Stop    Italian Restaurant   
285      Willowbrook              Bus Stop         Deli / Bodega   
286     Sandy Ground           Art Gallery                Market   
305        Fox Hills              Bus Stop        Sandwich Place   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
77                   Food        Ice Cream Shop        Sandwich Place   
198         Deli / Bodega        Discount Store            Playground   
202              Bus Stop         Women's Store           Fish Market   
205           Pizza Place              Bus Stop            Donut Shop   
224  Gym / Fitness Center           Coffee Shop    Athletics & Sports   
229   Japanese Restaurant           IT Services            Nail Salon   
241           Coffee Shop              Bus Stop   Filipino Restaurant   
242                 Diner              Bus Stop         Women's Store   
245            Theme Park              Bus Stop           Fish Market   
256                  Park           Pizza Place     Fish & Chips Shop   
258            Toll Plaza           Pizza Place         Deli / Bodega   
285            Bagel Shop    Chinese Restaurant           Pizza Place   
286          Liquor Store              Bus Stop           Fish Market   
305         Women's Store     Fish & Chips Shop           Event Space   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
77            Pizza Place            Playground                 Beach   
198           Flower Shop    Chinese Restaurant     Convenience Store   
202            Eye Doctor               Factory    Falafel Restaurant   
205   Filipino Restaurant               Exhibit            Eye Doctor   
224     Fish & Chips Shop               Exhibit            Eye Doctor   
229         Grocery Store                  Bank           Pizza Place   
241           Event Space               Exhibit            Eye Doctor   
242     Fish & Chips Shop               Exhibit            Eye Doctor   
245               Exhibit            Eye Doctor               Factory   
256               Exhibit            Eye Doctor               Factory   
258   American Restaurant        Ice Cream Shop           Gas Station   
285           Fish Market            Eye Doctor               Factory   
286               Exhibit            Eye Doctor               Factory   
305               Exhibit            Eye Doctor               Factory   

             9th Most Common Venue 10th Most Common Venue  
77                  Farmers Market    Filipino Restaurant  
198                  Bowling Alley             Food Stand  
202                           Farm         Farmers Market  
205                        Factory     Falafel Restaurant  
224                        Factory     Falafel Restaurant  
229  Vegetarian / Vegan Restaurant             Restaurant  
241                        Factory     Falafel Restaurant  
242                        Factory     Falafel Restaurant  
245             Falafel Restaurant                   Farm  
256             Falafel Restaurant                   Farm  
258                           Farm                  Field  
285             Falafel Restaurant                   Farm  
286            

CLUSTER 5

In [78]:
ny_merged.loc[ny_merged['Cluster Labels'] == 4, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
192   Somerville                  Park         Women's Store   
203    Todt Hill                 Trail                  Park   
303    Bayswater                  Park            Playground   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
192  Ethiopian Restaurant               Exhibit            Eye Doctor   
203         Women's Store   Filipino Restaurant           Event Space   
303          Tennis Court         Women's Store   Filipino Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
192               Factory    Falafel Restaurant                  Farm   
203               Exhibit            Eye Doctor               Factory   
303               Exhibit            Eye Doctor               Factory   

    9th Most Common Venue 10th Most Common Venue  
192        Farmers Market   Fast Food Restaurant  
203    Falafel Restaurant                   Farm  
303    Falafel Restaurant                   Farm

From the cluster data above, it looks like neighbourhoods in cluster 1 and 2 are more diverse and busy with business. They also seems like a mix of recidential and commercial/office spaces, which makes them more appropriate for starting cafe/restaurents. while cluster 3 and 5 indicates they have either limited/no public transport options available for public, seems to have a balance mix of outdoor activities, and a few businesses in the neighbourhood that would indicate these neighbourhoods to be mostly residential. Cluster 4 also, indicates mostly residential area with good public transports.
One interesting pattern that I noticed was, cluster 3,4,5 seems to include neighbourhoods with more frequently visited eye doctors. While this information alone, does not indicate any necessary problem, more exploration might provide more insight to why.

So If I am a tourist looking to explore nyc/am interested in starting a cafe or restaurant, I probably should concentrate more around the neighbourhoods in cluster 1 and 2.
